In [ ]:
import os
os.makedirs("geospatial", exist_ok=True)
print("Geospatial folder created!")


Geospatial folder created!


In [ ]:
!pip install geopy folium


In [ ]:
import pandas as pd

df = pd.read_csv(
    "/content/RESIDENTIAL_GOLD.csv",   # <-- your exact file name
    on_bad_lines='skip',               # skip corrupted rows
    engine='python'                    # more flexible parser
)

df.head()



PROPERTY_ID                                     NAME  \
0            0                         Casagrand ECR 14   
1            1    Ramanathan Nagar, Pozhichalur,Chennai   
2            2                              DAC Prapthi   
3            3  Naveenilaya,Chepauk, Triplicane,Chennai   
4            4                 VGN Spring Field Phase 1   

                                      PROPERTY_TITLE     PRICE  TOTAL_AREA  \
0  4 BHK Flat for sale in Kanathur Reddikuppam, C...  19900000        2583   
1  10 BHK Independent House for sale in Pozhichal...  22500000        7000   
2      3 BHK Flat for sale in West Tambaram, Chennai  10000000        1320   
3  7 BHK Independent House for sale in Triplicane...  33300000        4250   
4              2 BHK Flat for sale in Avadi, Chennai   4800000         960   

   PRICE_PER_SQFT  BATHS  BALCONY                                  LOCATION  \
0     7704.219899      4     True             Kanathur Reddikuppam, Chennai   
1     3214.285714      6     True     Ramanathan Nagar, Pozhichalur,Chennai   
2     7575.757576      3    False  Kasthuribai Nagar, West Tambaram,Chennai   
3     7835.294118      5     True   Naveenilaya,Chepauk, Triplicane,Chennai   
4     5000.000000      3     True                            Avadi, Chennai   

       CITY              LOCALITY  DESCRIPTION_LENGTH PRICE_CATEGORY  \
0   Chennai  Kanathur Reddikuppam                 603         Luxury   
1   Chennai      Ramanathan Nagar                 603         Luxury   
2   Chennai     Kasthuribai Nagar                 603      Mid Range   
3   Chennai           Naveenilaya                 603         Luxury   
4   Chennai                 Avadi                 603         Budget   

  BATH_CATEGORY                                        DESCRIPTION  
0       Premium  Best 4 BHK Apartment for modern-day lifestyle ...  
1       Premium  Looking for a 10 BHK Independent House for sal...  
2       Premium  Property for sale in Tambaram, Chennai. This 3...  
3       Premium  Entire Building for sale with 7 units of singl...  
4       Premium  Property for sale in Avadi, Chennai. This 2 BH...

In [ ]:
df.shape


(14528, 15)

In [ ]:
!pip install geopy

from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
import pandas as pd

geolocator = Nominatim(user_agent="real_estate_geocoder")
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)

# We will geocode this column
df['FULL_ADDRESS'] = df['LOCALITY'].astype(str) + ", " + df['CITY'].astype(str)

def get_lat(row):
    try:
        loc = geocode(row)
        return loc.latitude if loc else None
    except:
        return None

def get_lon(row):
    try:
        loc = geocode(row)
        return loc.longitude if loc else None
    except:
        return None

print("Extracting LAT/LON… (this will take several minutes)")
df['LAT'] = df['FULL_ADDRESS'].apply(get_lat)
df['LON'] = df['FULL_ADDRESS'].apply(get_lon)

df[['LOCALITY', 'CITY', 'LAT', 'LON']].head()


Extracting LAT/LON… (this will take several minutes)


In [ ]:
!pip install geopy

import pandas as pd
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
from tqdm import tqdm

tqdm.pandas()

# Load GOLD dataset
df = pd.read_csv("/content/RESIDENTIAL_GOLD.csv", on_bad_lines='skip', engine='python')

# Step 1: Top 300 localities
top_localities = df['LOCALITY'].value_counts().head(300).index.tolist()

# Create geo-lookup table using REAL CITY
geo_df = df[['LOCALITY', 'CITY']].drop_duplicates()

# Filter only top localities
geo_df = geo_df[geo_df['LOCALITY'].isin(top_localities)]

# Build accurate address
geo_df['FULL_ADDRESS'] = geo_df['LOCALITY'] + ", " + geo_df['CITY']

# Step 3 — Geocoder
geolocator = Nominatim(user_agent="real_estate_geocoder")
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)

latitudes = []
longitudes = []

print("Geocoding top 300 real addresses…")

for addr in tqdm(geo_df['FULL_ADDRESS']):
    try:
        loc = geocode(addr)
        latitudes.append(loc.latitude if loc else None)
        longitudes.append(loc.longitude if loc else None)
    except:
        latitudes.append(None)
        longitudes.append(None)

geo_df['LAT'] = latitudes
geo_df['LON'] = longitudes

geo_df.head(10)


Geocoding top 300 real addresses…


100%|██████████| 374/374 [06:35<00:00,  1.06s/it]


LOCALITY      CITY                   FULL_ADDRESS        LAT  \
4                 Avadi   Chennai                Avadi,  Chennai  13.093979   
7   Mahindra World City   Chennai  Mahindra World City,  Chennai        NaN   
18            Muttukadu   Chennai            Muttukadu,  Chennai  12.805902   
22            Mgr Nagar   Chennai             Mgr Nagar, Chennai  12.979583   
40           Arjunamedu   Chennai            Arjunamedu, Chennai        NaN   
44          Veppampattu   Chennai          Veppampattu,  Chennai  13.125815   
48          Madambakkam   Chennai          Madambakkam,  Chennai        NaN   
49            Urapakkam   Chennai            Urapakkam,  Chennai        NaN   
55    Ma. Po. Si. Nagar   Chennai     Ma. Po. Si. Nagar, Chennai        NaN   
69        Thirumangalam   Chennai         Thirumangalam, Chennai  13.085335   

          LON  
4   80.266405  
7         NaN  
18  80.242202  
22  80.249444  
40        NaN  
44  80.010147  
48        NaN  
49        NaN  
55        NaN  
69  80.201518

In [ ]:
geo_df.head()

LOCALITY      CITY                   FULL_ADDRESS        LAT  \
4                 Avadi   Chennai                Avadi,  Chennai  13.093979   
7   Mahindra World City   Chennai  Mahindra World City,  Chennai        NaN   
18            Muttukadu   Chennai            Muttukadu,  Chennai  12.805902   
22            Mgr Nagar   Chennai             Mgr Nagar, Chennai  12.979583   
40           Arjunamedu   Chennai            Arjunamedu, Chennai        NaN   

          LON  
4   80.266405  
7         NaN  
18  80.242202  
22  80.249444  
40        NaN

In [ ]:
# Merge geocoded data back into GOLD
df_geo = df.merge(geo_df[['LOCALITY','CITY','LAT','LON']],
                  on=['LOCALITY','CITY'],
                  how='left')

df_geo.head()


PROPERTY_ID                                     NAME  \
0            0                         Casagrand ECR 14   
1            1    Ramanathan Nagar, Pozhichalur,Chennai   
2            2                              DAC Prapthi   
3            3  Naveenilaya,Chepauk, Triplicane,Chennai   
4            4                 VGN Spring Field Phase 1   

                                      PROPERTY_TITLE     PRICE  TOTAL_AREA  \
0  4 BHK Flat for sale in Kanathur Reddikuppam, C...  19900000        2583   
1  10 BHK Independent House for sale in Pozhichal...  22500000        7000   
2      3 BHK Flat for sale in West Tambaram, Chennai  10000000        1320   
3  7 BHK Independent House for sale in Triplicane...  33300000        4250   
4              2 BHK Flat for sale in Avadi, Chennai   4800000         960   

   PRICE_PER_SQFT  BATHS  BALCONY                                  LOCATION  \
0     7704.219899      4     True             Kanathur Reddikuppam, Chennai   
1     3214.285714      6     True     Ramanathan Nagar, Pozhichalur,Chennai   
2     7575.757576      3    False  Kasthuribai Nagar, West Tambaram,Chennai   
3     7835.294118      5     True   Naveenilaya,Chepauk, Triplicane,Chennai   
4     5000.000000      3     True                            Avadi, Chennai   

       CITY              LOCALITY  DESCRIPTION_LENGTH PRICE_CATEGORY  \
0   Chennai  Kanathur Reddikuppam                 603         Luxury   
1   Chennai      Ramanathan Nagar                 603         Luxury   
2   Chennai     Kasthuribai Nagar                 603      Mid Range   
3   Chennai           Naveenilaya                 603         Luxury   
4   Chennai                 Avadi                 603         Budget   

  BATH_CATEGORY                                        DESCRIPTION        LAT  \
0       Premium  Best 4 BHK Apartment for modern-day lifestyle ...        NaN   
1       Premium  Looking for a 10 BHK Independent House for sal...        NaN   
2       Premium  Property for sale in Tambaram, Chennai. This 3...        NaN   
3       Premium  Entire Building for sale with 7 units of singl...        NaN   
4       Premium  Property for sale in Avadi, Chennai. This 2 BH...  13.093979   

         LON  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4  80.266405

In [ ]:
df_geo.to_csv("/content/RESIDENTIAL_GEO_ENRICHED.csv", index=False)
print("Saved RESIDENTIAL_GEO_ENRICHED.csv")


Saved RESIDENTIAL_GEO_ENRICHED.csv


In [ ]:
!pip install folium
from folium.plugins import HeatMap
import folium

# Remove rows without lat/lon
heat_df = df_geo.dropna(subset=['LAT','LON'])

# Create base map — centered on India
m = folium.Map(location=[20.5937, 78.9629], zoom_start=5)

# Heatmap points
heat_data = heat_df[['LAT','LON']].values.tolist()

HeatMap(heat_data, radius=10).add_to(m)

m


In [ ]:
# Price Map (Luxury → Red, Mid → Orange, Budget → Blue)

pm = folium.Map(location=[20.5937, 78.9629], zoom_start=5)

for _, row in heat_df.iterrows():
    folium.CircleMarker(
        location=[row['LAT'], row['LON']],
        radius=4,
        popup=f"{row['LOCALITY']} | ₹{row['PRICE']:,.0f}",
        color=(
            'blue' if row['PRICE'] < 5000000 else
            'orange' if row['PRICE'] < 15000000 else
            'red'
        ),
        fill=True,
        fill_opacity=0.6
    ).add_to(pm)

pm


In [ ]:
# Save heatmap
m.save("/content/heatmap_properties.html")

# Save price map
pm.save("/content/price_map_properties.html")

print("Both maps saved: heatmap_properties.html & price_map_properties.html")


Both maps saved: heatmap_properties.html & price_map_properties.html
